In [1]:
# !pip install altair
# !pip install altair_saver --upgrade
# !npm install -g vega-lite vega-cli canvas
# !pip install vl-convert-python --upgrade

In [2]:
# !pip install selenium --upgrade
# !apt-get install chromium-chromedriver -y

In [3]:
# !apt update
# !apt install ttf-mscorefonts-installer -y
# !apt reinstall fontconfig fontconfig-config libfontconfig1 -y

In [4]:
# !wget https://raw.githubusercontent.com/EconomicsObservatory/ECOvisualisations/main/guidelines/fonts/Circular/CircularStd-Black.otf -P /usr/local/share/fonts
# !wget https://raw.githubusercontent.com/EconomicsObservatory/ECOvisualisations/main/guidelines/fonts/Circular/CircularStd-Bold.otf -P /usr/local/share/fonts
# !wget https://raw.githubusercontent.com/EconomicsObservatory/ECOvisualisations/main/guidelines/fonts/Circular/CircularStd-Book.otf -P /usr/local/share/fonts
# !wget https://raw.githubusercontent.com/EconomicsObservatory/ECOvisualisations/main/guidelines/fonts/Circular/CircularStd-Medium.otf -P /usr/local/share/fonts

In [5]:
# !fc-cache -f

Enable large dataset support

In [6]:
# pip install "vegafusion[embed]"

In [7]:
import json
import altair as alt
from altair import expr, datum
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import requests
import urllib.parse

In [8]:
alt.data_transformers.enable("vegafusion")

DataTransformerRegistry.enable('vegafusion')

In [9]:
import colorsys
from matplotlib.colors import to_hex, to_rgb


def scale_lightness(rgb, scale_l):
    rgbhex = False
    if "#" in rgb:
        rgb = to_rgb(rgb)
        rgbhex = True
    # convert rgb to hls
    h, l, s = colorsys.rgb_to_hls(*rgb)
    # manipulate h, l, s values and return as rgb
    c = colorsys.hls_to_rgb(h, min(1, l * scale_l), s=s)
    if rgbhex:
        c = to_hex(c)
    return c

In [11]:
SAVE = False
LOCAL = True
DARK = True

if LOCAL:
    local_suffix = "_local"
else:
    local_suffix = ""

In [12]:
%%capture pwd
!pwd

In [13]:
uid = pwd.stdout.split("/")[-1].split("\r")[0]
uid=urllib.parse.quote(uid)
if not LOCAL:
    eco_git_home = (
        "https://raw.githubusercontent.com/EconomicsObservatory/ECOvisualisations/main/"
    )
    vega_embed = requests.get(eco_git_home + "guidelines/html/vega-embed.html").text
    colors = json.loads(
        requests.get(eco_git_home + "guidelines/colors/eco-colors.json").content
    )
    category_color = json.loads(
        requests.get(eco_git_home + "guidelines/colors/eco-category-color.json").content
    )
    hue_color = json.loads(
        requests.get(eco_git_home + "guidelines/colors/eco-single-hue-color.json").content
    )
    mhue_color = json.loads(
        requests.get(eco_git_home + "guidelines/colors/eco-multi-hue-color.json").content
    )
    div_color = json.loads(
        requests.get(eco_git_home + "guidelines/colors/eco-diverging-color.json").content
    )
    config = json.loads(
        requests.get(eco_git_home + "guidelines/charts/eco-global-config.json").content
    )
else:
    eco_git_home = '/'.join(pwd.stdout.split("/")[:-2])+'/'
    vega_embed = open(eco_git_home + "guidelines/html/vega-embed.html",'r').read()
    colors = json.load(
        open(eco_git_home + "guidelines/colors/eco-colors.json",'r')
    )
    category_color = json.load(
        open(eco_git_home + "guidelines/colors/eco-category-color.json",'r')
    )
    hue_color = json.load(
        open(eco_git_home + "guidelines/colors/eco-single-hue-color.json",'r')
    )
    mhue_color = json.load(
        open(eco_git_home + "guidelines/colors/eco-multi-hue-color.json",'r')
    )
    div_color = json.load(
        open(eco_git_home + "guidelines/colors/eco-diverging-color.json",'r')
    )
    config = json.load(
        open(eco_git_home + "guidelines/charts/eco-global-config.json",'r')
    )
eco_git_path = eco_git_home + "articles/" + uid + "/data/"
mo=0.5
height = config["height"]
width = config["width"]
uid, height, width

('devolution', 300, 500)

In [14]:
def save(df, f, LOCAL):
    fc = eco_git_path + f + ".csv"
    df.to_csv("data/" + f + ".csv")
    f += local_suffix
    open("visualisation/" + f + ".html", "w").write(
        vega_embed.replace(
            "JSON_PATH", fc.replace("/data/", "/visualisation/").replace(".csv", ".json")
        )
    )
    if LOCAL:
        fc = df
    
    from IPython.display import display, HTML
    display(HTML(df.head().to_html()))
    
    readme = "## Figure " + f.replace('fig','').split('_')[0] + \
        '  \n\nData: [`csv`](data/' + f + '.csv)' +\
        '  \nGitHub: [' + f + '](https://github.com/EconomicsObservatory/ECOvisualisations/tree/main/articles/'+uid +')'+\
        ''+\
        '  \n\n### Light theme  \n\nVersions with data locally embedded into the `Vega-lite` specification file: ' + \
        '[`png`](visualisation/' + f + '_local.png) [`svg`](visualisation/' + f + '_local.svg) [`json`](visualisation/' + f + '_local.json) '+ \
        '  \n (**Default**) Versions with data loaded from `GitHub`: ' + \
        '[`png`](visualisation/' + f + '.png) [`svg`](visualisation/' + f + '.svg) [`json`](visualisation/' + f + '.json)'+ \
        '  \nVersions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: ' + \
        '[`png`](visualisation/' + f + '_local_no_branding.png) [`svg`](visualisation/' + f + '_local_no_branding.svg) [`json`](visualisation/' + f + '_local_no_branding.json) '+ \
        '  \nVersions (no ECO branding) with data loaded from `GitHub`: ' + \
        '[`png`](visualisation/' + f + '_no_branding.png) [`svg`](visualisation/' + f + '_no_branding.svg) [`json`](visualisation/' + f + '_no_branding.json) '+ \
        ''+\
        '  \n\n### Dark theme  \n\nVersions with data locally embedded into the `Vega-lite` specification file: ' + \
        '[`png`](visualisation/' + f + '_local_dark.png) [`svg`](visualisation/' + f + '_local_dark.svg) [`json`](visualisation/' + f + '_local_dark.json) '+ \
        '  \n Versions with data loaded from `GitHub`: ' + \
        '[`png`](visualisation/' + f + '_dark.png) [`svg`](visualisation/' + f + '_dark.svg) [`json`](visualisation/' + f + '_dark.json)'+ \
        '  \nVersions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: ' + \
        '[`png`](visualisation/' + f + '_local_no_branding_dark.png) [`svg`](visualisation/' + f + '_local_no_branding_dark.svg) [`json`](visualisation/' + f + '_local_no_branding_dark.json) '+ \
        '  \nVersions (no ECO branding) with data loaded from `GitHub`: ' + \
        '[`png`](visualisation/' + f + '_no_branding_dark.png) [`svg`](visualisation/' + f + '_no_branding_dark.svg) [`json`](visualisation/' + f + '_no_branding_dark.json) '+ \
        ''+\
        '  \n\n!["' + f + '"](visualisation/' + f + '.svg "' + f + '")\n\n' +\
        '  \n\n!["' + f + '_dark"](visualisation/' + f + '_dark.svg "' + f + '")\n\n' 
    return readme, f, fc

In [15]:
def area(base,color,opacity=1):
    return base.mark_area(opacity=opacity,
    interpolate="monotone",
    line={'color':color},
    color=alt.Gradient(
        gradient='linear',
        stops=[alt.GradientStop(color='#ffffff00', offset=0.2),
               alt.GradientStop(color=color, offset=0.8)],
        x1=1, #0.8
        y1=1,
        x2=1,
        y2=0
        )
    )

In [16]:
# service_color='#d6c8da' '#e4bfe2' '#ce4b96' colors['eco-turquiose']
service_color='#b4c8d8'
def dark(f):
    configSource = "visualisation/" + f + ".json"
    config = json.loads(open(configSource, "r").read())
    config['background']=colors['eco-background']
    service_color='#b4c8d8'
    # for i in config['layer']:
    for i in config['hconcat']:
        if 'encoding' in i:
            for x in ['x','y']:
                if x in i['encoding']:
                    if 'axis' in i['encoding'][x]:
                        for c in ['domainColor','labelColor','tickColor','titleColor','gridColor']:
                            if c in i['encoding'][x]['axis']:
                                i['encoding'][x]['axis'][c]=service_color
        if 'mark' in i:
            if 'color' in i['mark']:
                if i['mark']['color']==colors['eco-gray']:
                    i['mark']['color']=service_color
                elif i['mark']['color']==colors['eco-blue']:
                    i['mark']['color']=colors['eco-yellow']
                elif i['mark']['color']==service_color:
                    i['mark']['color']=colors['eco-green']
                elif 'stops' in i['mark']['color']:
                    for s in i['mark']['color']['stops']:
                        if 'color' in s:
                            if s['color']==colors['eco-gray']:
                                s['color']=service_color
                            elif s['color']==colors['eco-blue']:
                                s['color']=colors['eco-yellow']
                            elif s['color']==service_color:
                                s['color']=colors['eco-green']
            if 'line' in i['mark']:
                if 'color' in i['mark']['line']:
                    if i['mark']['line']['color']==colors['eco-gray']:
                        i['mark']['line']['color']=service_color
                    elif i['mark']['line']['color']==colors['eco-blue']:
                        i['mark']['line']['color']=colors['eco-yellow']
                    elif i['mark']['line']['color']==service_color:
                        i['mark']['line']['color']=colors['eco-green']
            if 'stroke' in i['mark']:
                if i['mark']['stroke']=='white':
                    i['mark']['stroke']=colors['eco-background']
    if 'datasets' in config:
        for i in config['datasets']:
            if 'img' in config['datasets'][i][0]:
                if 'eco-icon-dark' in config['datasets'][i][0]['img']:
                    config['datasets'][i][0]['img']=config['datasets'][i][0]['img'].replace('eco-icon-dark','eco-icon-light')
    return alt.Chart.from_dict(config) 

# Fig 1

In [17]:
df = pd.read_csv("raw/devo.csv")
df=df.rename(columns={'Unnamed: 0':'Time'})
df=df.set_index(['Time','Group','Region','Gender']).stack().reset_index().rename(columns={'level_4':'Indicator',0:'Value'})
df['Keep4']=[True if i in ['1993-07-01','2023-07-01','2013-07-01','2003-07-01'] else False for i in df['Time']]
df['Keep2']=[True if i in ['1992-05-01','2023-07-01'] else False for i in df['Time']]

In [18]:
df1=df.set_index(['Time','Group','Region','Gender','Indicator']).loc['1992-05-01']['Value']
df2=df.set_index(['Time','Group','Region','Gender','Indicator']).loc['2023-07-01']['Value']
df3=(df2*100/df1)
df3=df3.reset_index()

In [19]:
df4=df3[df3['Gender']=='All']
df4['Value']=100
df4['Gender']='Reference'

/tmp/ipykernel_219/3494375145.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df4['Value']=100
/tmp/ipykernel_219/3494375145.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df4['Gender']='Reference'


In [20]:
df4=pd.concat([df3,df4])

In [21]:
readme, f, fc = save(df,"fig1_devo_trellis",LOCAL)

In [22]:
xmin='1992-05-01'
xmax='2023-07-01'

base = alt.Chart(fc).encode(x=alt.X(
        "Time:T",
        sort=[],
        axis=alt.Axis(
            grid=False,
            titleAlign="center",
            titleAnchor="middle",
            title="",
            titleY=-15,
            titleX=207,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            tickCount=10,
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            orient="bottom",
            labelAngle=0,
        ),
    ))\
    .transform_filter('datum.Group=="Aged 16+"')\
    .transform_filter('datum.Gender=="All"')\
    .transform_filter('datum.Region!="England"')\
    .transform_filter('datum.Region!="Great Britain"').transform_window(
    rolling_mean='mean(Value)',
    frame=[-7, 7],
    groupby=['Region']
)
    
line1=base.mark_line(size=4).encode(y=alt.Y('rolling_mean:Q',sort=[],
        axis=alt.Axis(
            # grid=False,
            gridDash=[1,5],
            gridColor=colors["eco-gray"],
            gridOpacity=mo,
            title="",
            titleX=0,
            titleY=-7,
            titleBaseline="bottom",
            titleAngle=0,
            titleAlign="left",
            ticks=False,
            labelPadding=5,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            format='s',
            tickCount=8
        )),
                                    color='Region:N')

layer1 = (
    (line1).facet(
    facet='Indicator:N',
    columns=3
).properties(title="").resolve_scale(
    y='independent'
)
    .configure(font='Circular Std Book').configure_view(stroke=None)
)


if DARK:
    layer1.save("visualisation/" + f + "_no_branding.json")
    layer2=dark(f+'_no_branding')
    layer2.save("visualisation/" + f + "_no_branding_dark.json")
    
if SAVE:
    layer1.save("visualisation/" + f + "_no_branding.json")
    layer1.save("visualisation/" + f + "_no_branding.svg")
    layer1.save("visualisation/" + f + "_no_branding.png")
    if DARK:
        layer2.save("visualisation/" + f + "_no_branding_dark.svg")
        layer2.save("visualisation/" + f + "_no_branding_dark.png")
    
logo=alt.Chart(pd.DataFrame([{"x": xmax, "y": 14, "img": "https://raw.githubusercontent.com/EconomicsObservatory/ECOvisualisations/main/guidelines/logos/eco-icon-dark.png"}]))\
    .mark_image(width=40,height=40,align='right',baseline='top',yOffset=-33,opacity=mo,xOffset=0).encode(x='x:T',y='y:Q',url='img:N')
# ecomark=alt.Chart(pd.DataFrame([{"x": '2019-01-01', "y": 14}]))\
#     .mark_point(size=100,fill=colors['eco-turquiose'],stroke=None,opacity=1,xOffset=-20,yOffset=-20).encode(x='x:T',y='y:Q')
# layer1+=(ecomark)
# layer1+=(logo)

if DARK:
    layer1.save("visualisation/" + f + ".json")
    layer2=dark(f)
    layer2.save("visualisation/" + f + "_dark.json")
if SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer1.save("visualisation/" + f + ".svg")
    layer1.save("visualisation/" + f + ".png")
    if DARK:
        layer2.save("visualisation/" + f + "_dark.svg")
        layer2.save("visualisation/" + f + "_dark.png")
    open("README.md", "w").write(readme)

print(f+'\n')
layer1.display()
if DARK:
    layer2.display()

KeyError: 'hconcat'

# Fig 2

In [249]:
xmin='1992-05-01'
xmax='2023-07-01'

age='Aged 16+'

base = alt.Chart(fc).encode(x=alt.X(
        "Time:T",
        sort=[],
        axis=alt.Axis(
            grid=False,
            titleAlign="center",
            titleAnchor="middle",
            title="",
            titleY=-15,
            titleX=207,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            tickCount=8,
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            orient="bottom",
            labelAngle=0,
        ),
    ))\
    .transform_filter('datum.Group=="'+age+'"')\
    .transform_filter('datum.Region!="England"')\
    .transform_filter('datum.Region!="Great Britain"').transform_window(
    rolling_mean='mean(Value)',
    frame=[-7, 7],
    groupby=['Region','Indicator']
)
    
lines=base.mark_line(size=4,opacity=0.2).encode(y=alt.Y('rolling_mean:Q',sort=[],
        axis=alt.Axis(
            # grid=False,
            gridDash=[1,5],
            gridColor=colors["eco-gray"],
            gridOpacity=mo,
            title="",
            titleX=0,
            titleY=-7,
            titleBaseline="bottom",
            titleAngle=0,
            titleAlign="left",
            ticks=False,
            labelPadding=5,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            format='s',
            tickCount=8
        )),
color=alt.Color('Region:N',legend=None))

ind='Unemployed'
line1a=lines.transform_filter('datum.Indicator=="'+ind+'"')
line1b=lines.mark_line(size=4,opacity=1).transform_filter('datum.Indicator=="'+ind+'"')\
    .transform_filter('datum.Keep2')

line1a_a=line1a.transform_filter('datum.Gender=="All"')
line1a_m=line1a.transform_filter('datum.Gender=="Men"')
line1a_w=line1a.transform_filter('datum.Gender=="Women"')

line1b_a=line1b.transform_filter('datum.Gender=="All"')
line1b_m=line1b.transform_filter('datum.Gender=="Men"')
line1b_w=line1b.transform_filter('datum.Gender=="Women"')


layer1_t = (
    (line1a_a+line1b_a).properties(title={'text':ind+', '+age+", All",'color':colors["eco-gray"]},width=450, height=300)
)

layer1_bl = (
    (line1a_m+line1b_m).properties(title={'text':"Men",'color':colors["eco-gray"]},width=200, height=150)
)

layer1_br = (
    (line1a_w+line1b_w).properties(title={'text':"Women",'color':colors["eco-gray"]},width=200, height=150)
)


if DARK:
    layer1.save("visualisation/" + f + "_no_branding.json")
    layer2=dark(f+'_no_branding')
    layer2.save("visualisation/" + f + "_no_branding_dark.json")
    
if SAVE:
    layer1.save("visualisation/" + f + "_no_branding.json")
    layer1.save("visualisation/" + f + "_no_branding.svg")
    layer1.save("visualisation/" + f + "_no_branding.png")
    if DARK:
        layer2.save("visualisation/" + f + "_no_branding_dark.svg")
        layer2.save("visualisation/" + f + "_no_branding_dark.png")
    
logo=alt.Chart(pd.DataFrame([{"x": xmax, "y": 14, "img": "https://raw.githubusercontent.com/EconomicsObservatory/ECOvisualisations/main/guidelines/logos/eco-icon-dark.png"}]))\
    .mark_image(width=40,height=40,align='right',baseline='top',yOffset=-33,opacity=mo,xOffset=0).encode(x='x:T',y='y:Q',url='img:N')
# ecomark=alt.Chart(pd.DataFrame([{"x": '2019-01-01', "y": 14}]))\
#     .mark_point(size=100,fill=colors['eco-turquiose'],stroke=None,opacity=1,xOffset=-20,yOffset=-20).encode(x='x:T',y='y:Q')
# layer1+=(ecomark)
layer1_t+=(logo)

layer1 = alt.vconcat(layer1_t,alt.hconcat(layer1_bl,layer1_br).resolve_scale(
    y='shared'
)).configure(font='Circular Std Book').configure_view(stroke=None)

if DARK:
    layer1.save("visualisation/" + f + ".json")
    layer2=dark(f)
    layer2.save("visualisation/" + f + "_dark.json")
if SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer1.save("visualisation/" + f + ".svg")
    layer1.save("visualisation/" + f + ".png")
    if DARK:
        layer2.save("visualisation/" + f + "_dark.svg")
        layer2.save("visualisation/" + f + "_dark.png")
    open("README.md", "w").write(readme)

print(f+'\n')
layer1.display()
if DARK:
    layer2.display()

fig1_devo_trellis_local



alt.VConcatChart(...)

# Fig 3

In [ ]:
import geopandas as gpd

# Load the UK map data
uk = gpd.read_file('https://raw.githubusercontent.com/EconomicsObservatory/courses/main/datasets/advanced/uk_itl1.geojson')

In [357]:
uk['ITL121NM']=uk['ITL121NM'].replace({
        'North East (England)': 'North East England',
        'North West (England)': 'North West England',
        'Yorkshire and The Humber': 'Yorkshire and the Humber',
        'East Midlands (England)': 'East Midlands',
        'West Midlands (England)': 'West Midlands',
        'East': 'East of England',
        'South East (England)': 'South East England',
        'South West (England)': 'South West England',
        'Wales': 'Wales',
        'Scotland': 'Scotland',
        'Northern Ireland': 'Northern Ireland'
    })

In [424]:
xmin='1992-05-01'
xmax='2023-07-01'

age='Aged 16+'

base = alt.Chart(fc).encode(x=alt.X(
        "Time:T",
        sort=[],
        axis=alt.Axis(
            grid=False,
            titleAlign="center",
            titleAnchor="middle",
            title="",
            titleY=-15,
            titleX=207,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            tickCount=8,
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            orient="bottom",
            labelAngle=0,
        ),
    ))\
    .transform_filter('datum.Group=="'+age+'"')\
    .transform_filter('datum.Region!="England"')\
    .transform_filter('datum.Region!="Great Britain"').transform_window(
    rolling_mean='mean(Value)',
    frame=[-7, 7],
    groupby=['Region','Indicator']
)
    
lines=base.mark_line(size=4,opacity=1).encode(y=alt.Y('rolling_mean:Q',sort=[],
        axis=alt.Axis(
            # grid=False,
            gridDash=[1,5],
            gridColor=colors["eco-gray"],
            gridOpacity=mo,
            title="",
            titleX=0,
            titleY=-7,
            titleBaseline="bottom",
            titleAngle=0,
            titleAlign="left",
            ticks=False,
            labelPadding=5,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            format='s',
            tickCount=8
        )),
color=alt.Color('Region:N',legend=None))

ind='Unemployed'
line1a=lines.transform_filter('datum.Indicator=="'+ind+'"')
line1b=lines.mark_line(size=4,opacity=1).transform_filter('datum.Indicator=="'+ind+'"')\
    .transform_filter('datum.Keep2')

line1a_a=line1a.transform_filter('datum.Gender=="All"')
line1a_m=line1a.transform_filter('datum.Gender=="Men"')
line1a_w=line1a.transform_filter('datum.Gender=="Women"')

line1b_a=line1b.transform_filter('datum.Gender=="All"')
line1b_m=line1b.transform_filter('datum.Gender=="Men"')
line1b_w=line1b.transform_filter('datum.Gender=="Women"')


layer1_t = (
    (line1a_a).properties(title={'text':ind+', '+age+", All",'color':colors["eco-gray"],'fontWeight':'normal','fontSize':12},width=450, height=300)
)

layer1_bl = (
    (line1a_m).properties(title={'text':"Men",'color':colors["eco-gray"],'fontWeight':'normal','fontSize':12},width=200, height=150)
)

layer1_br = (
    (line1a_w).properties(title={'text':"Women",'color':colors["eco-gray"],'fontWeight':'normal','fontSize':12},width=200, height=150)
)

spider=alt.Chart(df4).transform_filter(alt.FieldOneOfPredicate(field='Region', oneOf=['England','Wales','Scotland','Northern Ireland']))\
    .encode(x=alt.X(
        "Gender:N",
        sort=['Men','Reference','Women'],
        axis=alt.Axis(
            grid=False,
            titleAlign="center",
            titleAnchor="middle",
            title="",
            titleY=-15,
            titleX=207,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            tickCount=8,
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            orient="bottom",
            labelAngle=0,
        ),
    )).transform_filter('datum.Indicator=="'+ind+'"').transform_filter('datum.Group=="'+age+'"').transform_filter('datum.Gender!="All"')
spikes=spider.mark_line(size=4,opacity=1).encode(y=alt.Y('Value:Q',sort=[],
        axis=alt.Axis(
            # grid=False,
            gridDash=[1,5],
            gridColor=colors["eco-gray"],
            gridOpacity=mo,
            title="",
            titleX=0,
            titleY=-7,
            titleBaseline="bottom",
            titleAngle=0,
            titleAlign="left",
            ticks=False,
            labelPadding=5,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            format='s',
            tickCount=8,
            offset=-200
        ),
                                                        scale=alt.Scale(domain=[15,105])),
color=alt.Color('Region:N',legend=None)
)

points=spikes.mark_circle(size=110,opacity=1)
labels=spikes.mark_text(align='left',dx=5).encode(text='Region:N').transform_filter('datum.Gender=="Women"')

spike_layer=(spikes+points+labels).properties(title={'text':"Index change until 2023 May-Jul, since 1992 Mar-May = taken as 100",
    'color':colors["eco-gray"],'fontWeight':'normal','fontSize':12},width=400, height=200)

# Plot the UK map
map1 = alt.Chart(uk.join(df4[((df4['Indicator']==ind)&(df4['Group']==age)\
    &(df4['Gender']=='Men'))].set_index('Region')[['Value']],on='ITL121NM')).mark_geoshape(
    fill='lightgray',
    stroke='white'
).encode(fill=alt.Fill('Value:Q',title='',legend=alt.Legend(labelColor=colors["eco-gray"]),scale=alt.Scale(range=[colors['eco-dot'],colors["eco-gray"],colors['eco-turquiose']])))\
.project(
    type='identity',
    reflectY=True
).properties(title={'text':"Index change per region",'color':colors["eco-gray"],'fontWeight':'normal','fontSize':12,'dy':40},
    width=230,
    height=300
)

map2 = alt.Chart(uk.join(df4[((df4['Indicator']==ind)&(df4['Group']==age)\
    &(df4['Gender']=='Women'))].set_index('Region')[['Value']],on='ITL121NM')).mark_geoshape(
    fill='lightgray',
    stroke='white'
).encode(fill=alt.Fill('Value:Q',title='',legend=alt.Legend(labelColor=colors["eco-gray"],legendY=290,legendX=1000,orient='none'),scale=alt.Scale(range=[colors['eco-dot'],colors["eco-gray"],colors['eco-turquiose']])))\
.project(
    type='identity',
    reflectY=True
).properties(
    width=230,
    height=300
)

# if DARK:
#     layer1.save("visualisation/" + f + "_no_branding.json")
#     layer2=dark(f+'_no_branding')
#     layer2.save("visualisation/" + f + "_no_branding_dark.json")
    
# if SAVE:
#     layer1.save("visualisation/" + f + "_no_branding.json")
#     layer1.save("visualisation/" + f + "_no_branding.svg")
#     layer1.save("visualisation/" + f + "_no_branding.png")
#     if DARK:
#         layer2.save("visualisation/" + f + "_no_branding_dark.svg")
#         layer2.save("visualisation/" + f + "_no_branding_dark.png")
    
logo=alt.Chart(pd.DataFrame([{"x": xmax, "y": df[((df['Indicator']==ind)&(df['Group']==age)\
    &(df['Region']!='England')&(df['Region']!='Great Britain')&(df['Gender']=='All'))]['Value'].max(), "img": "https://raw.githubusercontent.com/EconomicsObservatory/ECOvisualisations/main/guidelines/logos/eco-icon-dark.png"}]))\
    .mark_image(width=40,height=40,align='right',baseline='top',yOffset=-33,opacity=mo,xOffset=0).encode(x=alt.X('x:T',axis=None),y=alt.Y('y:Q',axis=None),url='img:N')\
.properties(title='',width=50, height=50)
# ecomark=alt.Chart(pd.DataFrame([{"x": '2019-01-01', "y": 14}]))\
#     .mark_point(size=100,fill=colors['eco-turquiose'],stroke=None,opacity=1,xOffset=-20,yOffset=-20).encode(x='x:T',y='y:Q')
# layer1+=(ecomark)
# layer1_t+=(logo)

layer1 = alt.hconcat(alt.vconcat(layer1_t,alt.hconcat(layer1_bl,layer1_br).resolve_scale(
    y='shared'
)),alt.vconcat(alt.hconcat(spike_layer,logo),alt.hconcat(map1,map2))).configure(font='Circular Std Book').configure_view(stroke=None)

if DARK:
    layer1.save("visualisation/" + f + ".json")
    layer2=dark(f)
    layer2.save("visualisation/" + f + "_dark.json")
if SAVE:
    layer1.save("visualisation/" + f + ".json")
    layer1.save("visualisation/" + f + ".svg")
    layer1.save("visualisation/" + f + ".png")
    if DARK:
        layer2.save("visualisation/" + f + "_dark.svg")
        layer2.save("visualisation/" + f + "_dark.png")
    open("README.md", "w").write(readme)

print(f+'\n')
layer1.display()
if DARK:
    layer2.display()
    

Unexpected exception formatting exception. Falling back to standard exception


Traceback (most recent call last):
  File "/opt/conda/lib/python3.10/site-packages/IPython/core/interactiveshell.py", line 3508, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "/tmp/ipykernel_9657/3769670933.py", line 217, in <module>
    layer2.save("visualisation/" + f + "_dark.png")
  File "/opt/conda/lib/python3.10/site-packages/altair/vegalite/v5/api.py", line 1214, in save
    json_kwds=json_kwds,
  File "/opt/conda/lib/python3.10/site-packages/altair/utils/save.py", line 199, in save
    perform_save()
  File "/opt/conda/lib/python3.10/site-packages/altair/utils/save.py", line 169, in perform_save
    mimebundle = spec_to_mimebundle(
  File "/opt/conda/lib/python3.10/site-packages/altair/utils/mimebundle.py", line 70, in spec_to_mimebundle
    spec = compile_with_vegafusion(spec)
  File "/opt/conda/lib/python3.10/site-packages/altair/utils/_vegafusion_data.py", line 163, in compile_with_vegafusion
  File "/opt/conda/lib/python3.10/site-packages/vegafusi

In [426]:
xmin='1992-05-01'
xmax='2023-07-01'

age='Aged 16+'


base = alt.Chart(fc).encode(x=alt.X(
        "Time:T",
        sort=[],
        axis=alt.Axis(
            grid=False,
            titleAlign="center",
            titleAnchor="middle",
            title="",
            titleY=-15,
            titleX=207,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            tickCount=8,
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            orient="bottom",
            labelAngle=0,
        ),
    ))\
    .transform_filter('datum.Group=="'+age+'"')\
    .transform_filter('datum.Region!="England"')\
    .transform_filter('datum.Region!="Great Britain"').transform_window(
    rolling_mean='mean(Value)',
    frame=[-7, 7],
    groupby=['Region','Indicator']
)

lines=base.mark_line(size=4,opacity=1).encode(y=alt.Y('rolling_mean:Q',sort=[],
        axis=alt.Axis(
            # grid=False,
            gridDash=[1,5],
            gridColor=colors["eco-gray"],
            gridOpacity=mo,
            title="",
            titleX=0,
            titleY=-7,
            titleBaseline="bottom",
            titleAngle=0,
            titleAlign="left",
            ticks=False,
            labelPadding=5,
            labelColor=colors["eco-gray"],
            titleColor=colors["eco-gray"],
            tickColor=colors["eco-gray"],
            domainColor=colors["eco-gray"],
            domainOpacity=mo,
            tickOpacity=mo,
            labelOpacity=mo+0.2,
            titleOpacity=mo+0.3,
            titleFontSize=12,
            format='s',
            tickCount=8
        )),
color=alt.Color('Region:N',legend=None))

In [ ]:
for ind in df['Indicator']:
# ind=df['Indicator'][2]
    try:

        f='fig_'+ind

        line1a=lines.transform_filter('datum.Indicator=="'+ind+'"')
        line1b=lines.mark_line(size=4,opacity=1).transform_filter('datum.Indicator=="'+ind+'"')\
            .transform_filter('datum.Keep2')

        line1a_a=line1a.transform_filter('datum.Gender=="All"')
        line1a_m=line1a.transform_filter('datum.Gender=="Men"')
        line1a_w=line1a.transform_filter('datum.Gender=="Women"')

        line1b_a=line1b.transform_filter('datum.Gender=="All"')
        line1b_m=line1b.transform_filter('datum.Gender=="Men"')
        line1b_w=line1b.transform_filter('datum.Gender=="Women"')


        layer1_t = (
            (line1a_a).properties(title={'text':ind+', '+age+", All",'color':colors["eco-gray"],'fontWeight':'normal','fontSize':12},width=450, height=300)
        )

        layer1_bl = (
            (line1a_m).properties(title={'text':"Men",'color':colors["eco-gray"],'fontWeight':'normal','fontSize':12},width=200, height=150)
        )

        layer1_br = (
            (line1a_w).properties(title={'text':"Women",'color':colors["eco-gray"],'fontWeight':'normal','fontSize':12},width=200, height=150)
        )

        spider=alt.Chart(df4).transform_filter(alt.FieldOneOfPredicate(field='Region', oneOf=['England','Wales','Scotland','Northern Ireland']))\
            .encode(x=alt.X(
                "Gender:N",
                sort=['Men','Reference','Women'],
                axis=alt.Axis(
                    grid=False,
                    titleAlign="center",
                    titleAnchor="middle",
                    title="",
                    titleY=-15,
                    titleX=207,
                    labelColor=colors["eco-gray"],
                    titleColor=colors["eco-gray"],
                    tickColor=colors["eco-gray"],
                    domainColor=colors["eco-gray"],
                    tickCount=8,
                    domainOpacity=mo,
                    tickOpacity=mo,
                    labelOpacity=mo+0.2,
                    titleOpacity=mo+0.3,
                    titleFontSize=12,
                    orient="bottom",
                    labelAngle=0,
                ),
            )).transform_filter('datum.Indicator=="'+ind+'"').transform_filter('datum.Group=="'+age+'"').transform_filter('datum.Gender!="All"')
        spikes=spider.mark_line(size=4,opacity=1).encode(y=alt.Y('Value:Q',sort=[],
                axis=alt.Axis(
                    # grid=False,
                    gridDash=[1,5],
                    gridColor=colors["eco-gray"],
                    gridOpacity=mo,
                    title="",
                    titleX=0,
                    titleY=-7,
                    titleBaseline="bottom",
                    titleAngle=0,
                    titleAlign="left",
                    ticks=False,
                    labelPadding=5,
                    labelColor=colors["eco-gray"],
                    titleColor=colors["eco-gray"],
                    tickColor=colors["eco-gray"],
                    domainColor=colors["eco-gray"],
                    domainOpacity=mo,
                    tickOpacity=mo,
                    labelOpacity=mo+0.2,
                    titleOpacity=mo+0.3,
                    titleFontSize=12,
                    format='s',
                    tickCount=8,
                    offset=-200
                ),
                                                                # scale=alt.Scale(domain=[15,105])
                                                                ),
        color=alt.Color('Region:N',legend=None)
        )

        points=spikes.mark_circle(size=110,opacity=1)
        labels=spikes.mark_text(align='left',dx=5).encode(text='Region:N').transform_filter('datum.Gender=="Women"')

        spike_layer=(spikes+points+labels).properties(title={'text':"Index change until 2023 May-Jul, since 1992 Mar-May = taken as 100",
            'color':colors["eco-gray"],'fontWeight':'normal','fontSize':12},width=400, height=200)

        # Plot the UK map
        map1 = alt.Chart(uk.join(df4[((df4['Indicator']==ind)&(df4['Group']==age)\
            &(df4['Gender']=='Men'))].set_index('Region')[['Value']],on='ITL121NM')).mark_geoshape(
            fill='lightgray',
            stroke='white'
        ).encode(fill=alt.Fill('Value:Q',title='',legend=alt.Legend(labelColor=colors["eco-gray"]),scale=alt.Scale(range=[colors['eco-dot'],colors["eco-gray"],colors['eco-turquiose']])))\
        .project(
            type='identity',
            reflectY=True
        ).properties(title={'text':"Index change per region",'color':colors["eco-gray"],'fontWeight':'normal','fontSize':12,'dy':20},
            width=230,
            height=300
        )

        map2 = alt.Chart(uk.join(df4[((df4['Indicator']==ind)&(df4['Group']==age)\
            &(df4['Gender']=='Women'))].set_index('Region')[['Value']],on='ITL121NM')).mark_geoshape(
            fill='lightgray',
            stroke='white'
        ).encode(fill=alt.Fill('Value:Q',title='',legend=alt.Legend(labelColor=colors["eco-gray"],legendY=290,legendX=1000,orient='none'),scale=alt.Scale(range=[colors['eco-dot'],colors["eco-gray"],colors['eco-turquiose']])))\
        .project(
            type='identity',
            reflectY=True
        ).properties(
            width=230,
            height=300
        )

        # if DARK:
        #     layer1.save("visualisation/" + f + "_no_branding.json")
        #     layer2=dark(f+'_no_branding')
        #     layer2.save("visualisation/" + f + "_no_branding_dark.json")

        # if SAVE:
        #     layer1.save("visualisation/" + f + "_no_branding.json")
        #     layer1.save("visualisation/" + f + "_no_branding.svg")
        #     layer1.save("visualisation/" + f + "_no_branding.png")
        #     if DARK:
        #         layer2.save("visualisation/" + f + "_no_branding_dark.svg")
        #         layer2.save("visualisation/" + f + "_no_branding_dark.png")

        logo=alt.Chart(pd.DataFrame([{"x": xmax, "y": df[((df['Indicator']==ind)&(df['Group']==age)\
            &(df['Region']!='England')&(df['Region']!='Great Britain')&(df['Gender']=='All'))]['Value'].max(), "img": "https://raw.githubusercontent.com/EconomicsObservatory/ECOvisualisations/main/guidelines/logos/eco-icon-dark.png"}]))\
            .mark_image(width=40,height=40,align='right',baseline='top',yOffset=-33,opacity=mo,xOffset=0).encode(x=alt.X('x:T',axis=None),y=alt.Y('y:Q',axis=None),url='img:N')\
        .properties(title='',width=50, height=50)
        # ecomark=alt.Chart(pd.DataFrame([{"x": '2019-01-01', "y": 14}]))\
        #     .mark_point(size=100,fill=colors['eco-turquiose'],stroke=None,opacity=1,xOffset=-20,yOffset=-20).encode(x='x:T',y='y:Q')
        # layer1+=(ecomark)
        # layer1_t+=(logo)

        layer1 = alt.hconcat(alt.vconcat(layer1_t,alt.hconcat(layer1_bl,layer1_br).resolve_scale(
            y='shared'
        )),alt.vconcat(alt.hconcat(spike_layer,logo),alt.hconcat(map1,map2))).configure(font='Circular Std Book').configure_view(stroke=None)

        if DARK:
            layer1.save("visualisation/" + f + ".json")
            layer2=dark(f)
            layer2.save("visualisation/" + f + "_dark.json")
        if SAVE:
            layer1.save("visualisation/" + f + ".json")
            layer1.save("visualisation/" + f + ".svg")
            layer1.save("visualisation/" + f + ".png")
            if DARK:
                layer2.save("visualisation/" + f + "_dark.svg")
                layer2.save("visualisation/" + f + "_dark.png")
            open("README.md", "w").write(readme)

        print(f+'\n')
        # layer1.display()
        # if DARK:
        #     layer2.display()
    except: pass

In [407]:
# alt.Chart(uk.join(df4[((df4['Indicator']==ind)&(df4['Group']==age)\
#     &(df4['Gender']=='Women'))].set_index('Region')[['Value']],on='ITL121NM')).mark_geoshape(
#     fill='lightgray',
#     stroke='white'
# ).encode(fill=alt.Fill('Value:Q',title='',legend=alt.Legend(labelColor=colors["eco-gray"],legendY=400,orient='none'),scale=alt.Scale(range=[colors['eco-dot'],colors["eco-gray"],colors['eco-turquiose']])))\
# .project(
#     type='identity',
#     reflectY=True
# ).properties(title={'text':"Relative change per region",'color':colors["eco-gray"],'fontWeight':'normal','fontSize':12, 'dy':50},
#     width=250,
#     height=300
# )

# Fig 4

# Post-process

## Clean up `SVG`s
`base64 URI` encode images

In [39]:
from base64 import b64encode

In [40]:
from os import listdir
from os.path import isfile, join
mypath='./visualisation/'
onlyfiles = [f for f in listdir(mypath) if isfile(join(mypath, f))]
svgs=[i for i in onlyfiles if i[-4:]=='.svg']

In [41]:
for svg in svgs:
    s=open(mypath+svg,'r').read()
    si=s.find('"image mark" xlink:href=')
    if si>-1:
        s2=s[si+25:]
        imgurl=s2[:s2.find('"')]
        if 'data:image/png;' not in imgurl:
            s1=s[:si+25]+s2.replace(imgurl,'data:image/png;base64,'+b64encode(requests.get(imgurl).content).decode('utf-8'))
            open(mypath+svg,'w').write(s1)
            print(svg)

fig1_cpi.svg
fig1_cpi_dark.svg
fig2_boe_rate.svg
fig2_boe_rate_dark.svg
fig3_pay.svg
fig3_pay_dark.svg
fig4_asda.svg
fig4_asda_dark.svg
fig5_quint.svg
fig5_quint_dark.svg
fig6_food.svg
fig6_food_dark.svg
fig7_gfk.svg
fig7_gfk_dark.svg
fig8_gifts.svg
fig8_gifts_dark.svg


## README

In [49]:
from IPython.display import display, Markdown

with open('README.md', 'r') as fh:
    content = fh.read()

display(Markdown(content))

## Figure 1  

Data: [`csv`](data/fig1_cpi.csv)  
GitHub: [fig1_cpi](https://github.com/EconomicsObservatory/ECOvisualisations/tree/main/articles/how-is-consumer-spending-around-christmas-2023-likely-to-affect-retailers)  

### Light theme  

Versions with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig1_cpi_local.png) [`svg`](visualisation/fig1_cpi_local.svg) [`json`](visualisation/fig1_cpi_local.json)   
 (**Default**) Versions with data loaded from `GitHub`: [`png`](visualisation/fig1_cpi.png) [`svg`](visualisation/fig1_cpi.svg) [`json`](visualisation/fig1_cpi.json)  
Versions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig1_cpi_local_no_branding.png) [`svg`](visualisation/fig1_cpi_local_no_branding.svg) [`json`](visualisation/fig1_cpi_local_no_branding.json)   
Versions (no ECO branding) with data loaded from `GitHub`: [`png`](visualisation/fig1_cpi_no_branding.png) [`svg`](visualisation/fig1_cpi_no_branding.svg) [`json`](visualisation/fig1_cpi_no_branding.json)   

### Dark theme  

Versions with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig1_cpi_local_dark.png) [`svg`](visualisation/fig1_cpi_local_dark.svg) [`json`](visualisation/fig1_cpi_local_dark.json)   
 Versions with data loaded from `GitHub`: [`png`](visualisation/fig1_cpi_dark.png) [`svg`](visualisation/fig1_cpi_dark.svg) [`json`](visualisation/fig1_cpi_dark.json)  
Versions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig1_cpi_local_no_branding_dark.png) [`svg`](visualisation/fig1_cpi_local_no_branding_dark.svg) [`json`](visualisation/fig1_cpi_local_no_branding_dark.json)   
Versions (no ECO branding) with data loaded from `GitHub`: [`png`](visualisation/fig1_cpi_no_branding_dark.png) [`svg`](visualisation/fig1_cpi_no_branding_dark.svg) [`json`](visualisation/fig1_cpi_no_branding_dark.json)   

!["fig1_cpi"](visualisation/fig1_cpi.svg "fig1_cpi")

  

!["fig1_cpi_dark"](visualisation/fig1_cpi_dark.svg "fig1_cpi")

## Figure 2  

Data: [`csv`](data/fig2_boe_rate.csv)  
GitHub: [fig2_boe_rate](https://github.com/EconomicsObservatory/ECOvisualisations/tree/main/articles/how-is-consumer-spending-around-christmas-2023-likely-to-affect-retailers)  

### Light theme  

Versions with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig2_boe_rate_local.png) [`svg`](visualisation/fig2_boe_rate_local.svg) [`json`](visualisation/fig2_boe_rate_local.json)   
 (**Default**) Versions with data loaded from `GitHub`: [`png`](visualisation/fig2_boe_rate.png) [`svg`](visualisation/fig2_boe_rate.svg) [`json`](visualisation/fig2_boe_rate.json)  
Versions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig2_boe_rate_local_no_branding.png) [`svg`](visualisation/fig2_boe_rate_local_no_branding.svg) [`json`](visualisation/fig2_boe_rate_local_no_branding.json)   
Versions (no ECO branding) with data loaded from `GitHub`: [`png`](visualisation/fig2_boe_rate_no_branding.png) [`svg`](visualisation/fig2_boe_rate_no_branding.svg) [`json`](visualisation/fig2_boe_rate_no_branding.json)   

### Dark theme  

Versions with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig2_boe_rate_local_dark.png) [`svg`](visualisation/fig2_boe_rate_local_dark.svg) [`json`](visualisation/fig2_boe_rate_local_dark.json)   
 Versions with data loaded from `GitHub`: [`png`](visualisation/fig2_boe_rate_dark.png) [`svg`](visualisation/fig2_boe_rate_dark.svg) [`json`](visualisation/fig2_boe_rate_dark.json)  
Versions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig2_boe_rate_local_no_branding_dark.png) [`svg`](visualisation/fig2_boe_rate_local_no_branding_dark.svg) [`json`](visualisation/fig2_boe_rate_local_no_branding_dark.json)   
Versions (no ECO branding) with data loaded from `GitHub`: [`png`](visualisation/fig2_boe_rate_no_branding_dark.png) [`svg`](visualisation/fig2_boe_rate_no_branding_dark.svg) [`json`](visualisation/fig2_boe_rate_no_branding_dark.json)   

!["fig2_boe_rate"](visualisation/fig2_boe_rate.svg "fig2_boe_rate")

  

!["fig2_boe_rate_dark"](visualisation/fig2_boe_rate_dark.svg "fig2_boe_rate")

## Figure 3  

Data: [`csv`](data/fig3_pay.csv)  
GitHub: [fig3_pay](https://github.com/EconomicsObservatory/ECOvisualisations/tree/main/articles/how-is-consumer-spending-around-christmas-2023-likely-to-affect-retailers)  

### Light theme  

Versions with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig3_pay_local.png) [`svg`](visualisation/fig3_pay_local.svg) [`json`](visualisation/fig3_pay_local.json)   
 (**Default**) Versions with data loaded from `GitHub`: [`png`](visualisation/fig3_pay.png) [`svg`](visualisation/fig3_pay.svg) [`json`](visualisation/fig3_pay.json)  
Versions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig3_pay_local_no_branding.png) [`svg`](visualisation/fig3_pay_local_no_branding.svg) [`json`](visualisation/fig3_pay_local_no_branding.json)   
Versions (no ECO branding) with data loaded from `GitHub`: [`png`](visualisation/fig3_pay_no_branding.png) [`svg`](visualisation/fig3_pay_no_branding.svg) [`json`](visualisation/fig3_pay_no_branding.json)   

### Dark theme  

Versions with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig3_pay_local_dark.png) [`svg`](visualisation/fig3_pay_local_dark.svg) [`json`](visualisation/fig3_pay_local_dark.json)   
 Versions with data loaded from `GitHub`: [`png`](visualisation/fig3_pay_dark.png) [`svg`](visualisation/fig3_pay_dark.svg) [`json`](visualisation/fig3_pay_dark.json)  
Versions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig3_pay_local_no_branding_dark.png) [`svg`](visualisation/fig3_pay_local_no_branding_dark.svg) [`json`](visualisation/fig3_pay_local_no_branding_dark.json)   
Versions (no ECO branding) with data loaded from `GitHub`: [`png`](visualisation/fig3_pay_no_branding_dark.png) [`svg`](visualisation/fig3_pay_no_branding_dark.svg) [`json`](visualisation/fig3_pay_no_branding_dark.json)   

!["fig3_pay"](visualisation/fig3_pay.svg "fig3_pay")

  

!["fig3_pay_dark"](visualisation/fig3_pay_dark.svg "fig3_pay")

## Figure 4  

Data: [`csv`](data/fig4_asda.csv)  
GitHub: [fig4_asda](https://github.com/EconomicsObservatory/ECOvisualisations/tree/main/articles/how-is-consumer-spending-around-christmas-2023-likely-to-affect-retailers)  

### Light theme  

Versions with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig4_asda_local.png) [`svg`](visualisation/fig4_asda_local.svg) [`json`](visualisation/fig4_asda_local.json)   
 (**Default**) Versions with data loaded from `GitHub`: [`png`](visualisation/fig4_asda.png) [`svg`](visualisation/fig4_asda.svg) [`json`](visualisation/fig4_asda.json)  
Versions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig4_asda_local_no_branding.png) [`svg`](visualisation/fig4_asda_local_no_branding.svg) [`json`](visualisation/fig4_asda_local_no_branding.json)   
Versions (no ECO branding) with data loaded from `GitHub`: [`png`](visualisation/fig4_asda_no_branding.png) [`svg`](visualisation/fig4_asda_no_branding.svg) [`json`](visualisation/fig4_asda_no_branding.json)   

### Dark theme  

Versions with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig4_asda_local_dark.png) [`svg`](visualisation/fig4_asda_local_dark.svg) [`json`](visualisation/fig4_asda_local_dark.json)   
 Versions with data loaded from `GitHub`: [`png`](visualisation/fig4_asda_dark.png) [`svg`](visualisation/fig4_asda_dark.svg) [`json`](visualisation/fig4_asda_dark.json)  
Versions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig4_asda_local_no_branding_dark.png) [`svg`](visualisation/fig4_asda_local_no_branding_dark.svg) [`json`](visualisation/fig4_asda_local_no_branding_dark.json)   
Versions (no ECO branding) with data loaded from `GitHub`: [`png`](visualisation/fig4_asda_no_branding_dark.png) [`svg`](visualisation/fig4_asda_no_branding_dark.svg) [`json`](visualisation/fig4_asda_no_branding_dark.json)   

!["fig4_asda"](visualisation/fig4_asda.svg "fig4_asda")

  

!["fig4_asda_dark"](visualisation/fig4_asda_dark.svg "fig4_asda")

## Figure 5  

Data: [`csv`](data/fig5_quint.csv)  
GitHub: [fig5_quint](https://github.com/EconomicsObservatory/ECOvisualisations/tree/main/articles/how-is-consumer-spending-around-christmas-2023-likely-to-affect-retailers)  

### Light theme  

Versions with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig5_quint_local.png) [`svg`](visualisation/fig5_quint_local.svg) [`json`](visualisation/fig5_quint_local.json)   
 (**Default**) Versions with data loaded from `GitHub`: [`png`](visualisation/fig5_quint.png) [`svg`](visualisation/fig5_quint.svg) [`json`](visualisation/fig5_quint.json)  
Versions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig5_quint_local_no_branding.png) [`svg`](visualisation/fig5_quint_local_no_branding.svg) [`json`](visualisation/fig5_quint_local_no_branding.json)   
Versions (no ECO branding) with data loaded from `GitHub`: [`png`](visualisation/fig5_quint_no_branding.png) [`svg`](visualisation/fig5_quint_no_branding.svg) [`json`](visualisation/fig5_quint_no_branding.json)   

### Dark theme  

Versions with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig5_quint_local_dark.png) [`svg`](visualisation/fig5_quint_local_dark.svg) [`json`](visualisation/fig5_quint_local_dark.json)   
 Versions with data loaded from `GitHub`: [`png`](visualisation/fig5_quint_dark.png) [`svg`](visualisation/fig5_quint_dark.svg) [`json`](visualisation/fig5_quint_dark.json)  
Versions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig5_quint_local_no_branding_dark.png) [`svg`](visualisation/fig5_quint_local_no_branding_dark.svg) [`json`](visualisation/fig5_quint_local_no_branding_dark.json)   
Versions (no ECO branding) with data loaded from `GitHub`: [`png`](visualisation/fig5_quint_no_branding_dark.png) [`svg`](visualisation/fig5_quint_no_branding_dark.svg) [`json`](visualisation/fig5_quint_no_branding_dark.json)   

!["fig5_quint"](visualisation/fig5_quint.svg "fig5_quint")

  

!["fig5_quint_dark"](visualisation/fig5_quint_dark.svg "fig5_quint")

## Figure 6  

Data: [`csv`](data/fig6_food.csv)  
GitHub: [fig6_food](https://github.com/EconomicsObservatory/ECOvisualisations/tree/main/articles/how-is-consumer-spending-around-christmas-2023-likely-to-affect-retailers)  

### Light theme  

Versions with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig6_food_local.png) [`svg`](visualisation/fig6_food_local.svg) [`json`](visualisation/fig6_food_local.json)   
 (**Default**) Versions with data loaded from `GitHub`: [`png`](visualisation/fig6_food.png) [`svg`](visualisation/fig6_food.svg) [`json`](visualisation/fig6_food.json)  
Versions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig6_food_local_no_branding.png) [`svg`](visualisation/fig6_food_local_no_branding.svg) [`json`](visualisation/fig6_food_local_no_branding.json)   
Versions (no ECO branding) with data loaded from `GitHub`: [`png`](visualisation/fig6_food_no_branding.png) [`svg`](visualisation/fig6_food_no_branding.svg) [`json`](visualisation/fig6_food_no_branding.json)   

### Dark theme  

Versions with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig6_food_local_dark.png) [`svg`](visualisation/fig6_food_local_dark.svg) [`json`](visualisation/fig6_food_local_dark.json)   
 Versions with data loaded from `GitHub`: [`png`](visualisation/fig6_food_dark.png) [`svg`](visualisation/fig6_food_dark.svg) [`json`](visualisation/fig6_food_dark.json)  
Versions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig6_food_local_no_branding_dark.png) [`svg`](visualisation/fig6_food_local_no_branding_dark.svg) [`json`](visualisation/fig6_food_local_no_branding_dark.json)   
Versions (no ECO branding) with data loaded from `GitHub`: [`png`](visualisation/fig6_food_no_branding_dark.png) [`svg`](visualisation/fig6_food_no_branding_dark.svg) [`json`](visualisation/fig6_food_no_branding_dark.json)   

!["fig6_food"](visualisation/fig6_food.svg "fig6_food")

  

!["fig6_food_dark"](visualisation/fig6_food_dark.svg "fig6_food")

## Figure 7  

Data: [`csv`](data/fig7_gfk.csv)  
GitHub: [fig7_gfk](https://github.com/EconomicsObservatory/ECOvisualisations/tree/main/articles/how-is-consumer-spending-around-christmas-2023-likely-to-affect-retailers)  

### Light theme  

Versions with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig7_gfk_local.png) [`svg`](visualisation/fig7_gfk_local.svg) [`json`](visualisation/fig7_gfk_local.json)   
 (**Default**) Versions with data loaded from `GitHub`: [`png`](visualisation/fig7_gfk.png) [`svg`](visualisation/fig7_gfk.svg) [`json`](visualisation/fig7_gfk.json)  
Versions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig7_gfk_local_no_branding.png) [`svg`](visualisation/fig7_gfk_local_no_branding.svg) [`json`](visualisation/fig7_gfk_local_no_branding.json)   
Versions (no ECO branding) with data loaded from `GitHub`: [`png`](visualisation/fig7_gfk_no_branding.png) [`svg`](visualisation/fig7_gfk_no_branding.svg) [`json`](visualisation/fig7_gfk_no_branding.json)   

### Dark theme  

Versions with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig7_gfk_local_dark.png) [`svg`](visualisation/fig7_gfk_local_dark.svg) [`json`](visualisation/fig7_gfk_local_dark.json)   
 Versions with data loaded from `GitHub`: [`png`](visualisation/fig7_gfk_dark.png) [`svg`](visualisation/fig7_gfk_dark.svg) [`json`](visualisation/fig7_gfk_dark.json)  
Versions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig7_gfk_local_no_branding_dark.png) [`svg`](visualisation/fig7_gfk_local_no_branding_dark.svg) [`json`](visualisation/fig7_gfk_local_no_branding_dark.json)   
Versions (no ECO branding) with data loaded from `GitHub`: [`png`](visualisation/fig7_gfk_no_branding_dark.png) [`svg`](visualisation/fig7_gfk_no_branding_dark.svg) [`json`](visualisation/fig7_gfk_no_branding_dark.json)   

!["fig7_gfk"](visualisation/fig7_gfk.svg "fig7_gfk")

  

!["fig7_gfk_dark"](visualisation/fig7_gfk_dark.svg "fig7_gfk")

## Figure 8  

Data: [`csv`](data/fig8_gifts.csv)  
GitHub: [fig8_gifts](https://github.com/EconomicsObservatory/ECOvisualisations/tree/main/articles/how-is-consumer-spending-around-christmas-2023-likely-to-affect-retailers)  

### Light theme  

Versions with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig8_gifts_local.png) [`svg`](visualisation/fig8_gifts_local.svg) [`json`](visualisation/fig8_gifts_local.json)   
 (**Default**) Versions with data loaded from `GitHub`: [`png`](visualisation/fig8_gifts.png) [`svg`](visualisation/fig8_gifts.svg) [`json`](visualisation/fig8_gifts.json)  
Versions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig8_gifts_local_no_branding.png) [`svg`](visualisation/fig8_gifts_local_no_branding.svg) [`json`](visualisation/fig8_gifts_local_no_branding.json)   
Versions (no ECO branding) with data loaded from `GitHub`: [`png`](visualisation/fig8_gifts_no_branding.png) [`svg`](visualisation/fig8_gifts_no_branding.svg) [`json`](visualisation/fig8_gifts_no_branding.json)   

### Dark theme  

Versions with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig8_gifts_local_dark.png) [`svg`](visualisation/fig8_gifts_local_dark.svg) [`json`](visualisation/fig8_gifts_local_dark.json)   
 Versions with data loaded from `GitHub`: [`png`](visualisation/fig8_gifts_dark.png) [`svg`](visualisation/fig8_gifts_dark.svg) [`json`](visualisation/fig8_gifts_dark.json)  
Versions (no ECO branding) with data locally embedded into the `Vega-lite` specification file: [`png`](visualisation/fig8_gifts_local_no_branding_dark.png) [`svg`](visualisation/fig8_gifts_local_no_branding_dark.svg) [`json`](visualisation/fig8_gifts_local_no_branding_dark.json)   
Versions (no ECO branding) with data loaded from `GitHub`: [`png`](visualisation/fig8_gifts_no_branding_dark.png) [`svg`](visualisation/fig8_gifts_no_branding_dark.svg) [`json`](visualisation/fig8_gifts_no_branding_dark.json)   

!["fig8_gifts"](visualisation/fig8_gifts.svg "fig8_gifts")

  

!["fig8_gifts_dark"](visualisation/fig8_gifts_dark.svg "fig8_gifts")

  

## Infographics  
Summary auto-generated using [ChatGPT](https://chat.openai.com/)    

### Light theme  

!["fig8_gifts"](visualisation/collage_light.png " collage_light")  

### Dark theme  

!["fig8_gifts"](visualisation/collage_dark.png " collage_dark")